In [92]:
from pandas_datareader import data as pdr
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import yfinance as yf
import json
import threading
import logging
yf.pdr_override() # <== that's all it takes :-)
logging.basicConfig(level=logging.INFO, filename='load_data.log')

In [18]:
hk_tickers=pd.read_csv('HKTickers.csv')

In [19]:
hk_tickers=yf.Tickers(hk_tickers.Tickers.to_list())

In [72]:
len(hk_tickers.tickers)

2464

In [78]:
def appendToTickersInfo(arange):
    global tickersInfo
    for t in arange:
        try:
            tickersInfo.append(hk_tickers.tickers[t].info)
            if (t%100==0): logging.info("Adding tickers[" + str(t) + "]")
        except:
            pass

def dumpTickersInfoToFile(filename):
    global tickersInfo
    with open(filename, 'w') as file:
        file.write(json.dumps(tickersInfo))
        
def loadTickersInfoFromFile(filename):
    global tickersInfo
    with open(filename, 'r') as file:
        tickersInfo=json.loads(file.read())

In [62]:
class DownloadThread (threading.Thread):
   def __init__(self, threadID, name, arange):
      threading.Thread.__init__(self)
      self.threadID = threadID
      self.name = name
      self.arange = arange
   def run(self):
      logging.info("Starting " + self.name)
      appendToTickersInfo(self.arange)
      logging.info("Exiting " + self.name)

In [63]:
tickersInfo=[]
batchSize=300
threads = [DownloadThread(i, 'T'+str(i), range(batchSize*i,batchSize*(i+1))) for i in range(int(len(hk_tickers.tickers) / batchSize)+1)]
for t in threads:
    t.start()

In [82]:
# dumpTickersInfoToFile('HKTickersAttributes.json')
loadTickersInfoFromFile('HKTickersAttributes.json')

In [129]:
len(tickersInfo)

2318

In [134]:
def getValue(info, key):
    if(key in info): 
        return info[key]
    else:
        return np.nan

selected_keys=['symbol', 'sector', 'industry', 'longName', 'volume', 
               'profitMargins', 'sharesOutstanding', 'regularMarketPreviousClose', 'trailingPE', 'priceToBook']
tickersFrame = pd.DataFrame(data=[],columns=selected_keys)

for t in tickersInfo:
    s={key: getValue(t, key) for key in selected_keys}
    tickersFrame=tickersFrame.append(s, ignore_index=True)

tickersFrame.set_index(['symbol'], inplace=True)
tickersFrame.sort_index(inplace=True)

In [140]:
tickersFrame[tickersFrame.notna().all(axis=1)]
tickersFrame

sector                        industry  \
symbol                                                            
0001.HK             Industrials                   Conglomerates   
0002.HK               Utilities    Utilities—Regulated Electric   
0003.HK               Utilities         Utilities—Regulated Gas   
0004.HK             Real Estate            Real Estate Services   
0005.HK      Financial Services               Banks—Diversified   
...                         ...                             ...   
8627.HK  Communication Services            Advertising Agencies   
8631.HK                  Energy  Oil & Gas Refining & Marketing   
8635.HK              Technology            Software—Application   
8668.HK       Consumer Cyclical                         Leisure   
9988.HK       Consumer Cyclical                 Internet Retail   

                                            longName   volume  profitMargins  \
symbol                                                                         
0001.HK                CK Hutchison Holdings Limited   700952        0.13379   
0002.HK                         CLP Holdings Limited   785501        0.06145   
0003.HK  The Hong Kong and China Gas Company Limited  5314320        0.21171   
0004.HK                     Wharf (Holdings) Limited   245632        0.29174   
0005.HK                            HSBC Holdings plc  1567607        0.27508   
...                                              ...      ...            ...   
8627.HK         Orange Tour Cultural Holding Limited  1104000        0.25478   
8631.HK                    Sun Kong Holdings Limited   480000       -0.00551   
8635.HK             Novacon Technology Group Limited   100000        0.13313   
8668.HK      Ying Hai Group Holdings Company Limited   180000        0.02313   
9988.HK                Alibaba Group Holding Limited  1112842        0.34420   

        sharesOutstanding  regularMarketPreviousClose trailingPE priceToBook  
symbol                                                                        
0001.HK        3856240128                      69.700    6.87438    0.590349  
0002.HK        2526449920                      79.200    14.9254     1.83967  
0003.HK       16925100032                      14.740    26.9091     3.84416  
0004.HK        3049029888                      17.880    8.18349    0.381417  
0005.HK       20312600576                      57.600    11.7113     6.15811  
...                   ...                         ...        ...         ...  
8627.HK         800000000                       0.820        NaN        None  
8631.HK         400000000                       0.241        NaN     1.47853  
8635.HK         400000000                       0.126        NaN    0.533898  
8668.HK        1200000000                       0.165        NaN     3.86364  
9988.HK       21461800960                     195.400        NaN        None  

[2318 rows x 9 columns]

In [141]:
tickersFrame.to_csv('HKTickersAttributes.csv')

In [83]:
t = yf.Ticker('80737.HK')
t.actions
t.balance_sheet
t.financials
t.cashflow
tickersInfo

[{'sector': 'Technology',
  'fullTimeEmployees': 4800,
  'longBusinessSummary': 'Computime Group Limited, an investment holding company, engages in the research, development, design, manufacture, and trading of electronic control products in the Americas, Europe, and Asia. It operates through two segments, Smart Solutions and Contract Manufacturing Services. The company researches, designs, develops, manufactures, trades in, and distributes building and home control; appliance control; and commercial and industrial control products. It also offers a range of services, including software, electronics, PCB layout, mechanical design, front-end interface development, mechanical package design, advanced test development, product industrialization, assembly, and mass production. In addition, the company provides original equipment and design manufacturing services in various market segments, such as appliance controls; heating, ventilating, air conditioning, and refrigeration; and commercial

In [ ]:
msft = yf.Ticker("MSFT")

# get stock info
msft.info

# get historical market data
hist = msft.history(period="max")

# show actions (dividends, splits)
msft.actions

# show dividends
msft.dividends

# show splits
msft.splits

# show financials
msft.financials
msft.quarterly_financials

# show balance heet
msft.balance_sheet
msft.quarterly_balance_sheet

# show cashflow
msft.cashflow
msft.quarterly_cashflow

# show earnings
msft.earnings
msft.quarterly_earnings

# show sustainability
msft.sustainability

# show analysts recommendations
msft.recommendations

# show next event (earnings, etc)
msft.calendar

# show options expirations


# get option chain for specific expiration
# opt = msft.option_chain('2019-12-06')
# data available via: opt.calls, opt.puts

In [ ]:
msft.earnings['ProfitRatio']=msft.earnings['Earnings']/msft.earnings['Revenue']

In [ ]:
msft.earnings

In [ ]:
data = pdr.get_data_yahoo("MSFT", start="2010-01-01", end="2017-04-30")

In [ ]:
data

In [ ]:
data = yf.download("SPY AAPL", start="2017-01-01", end="2017-04-30",
                   group_by="ticker")

In [ ]:
data